# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 517, done.
remote: Counting objects: 100% (124/124), done.
remote: Compressing objects: 100% (59/59), done.
remote: Total 517 (delta 65), reused 121 (delta 64), pack-reused 393
Receiving objects: 100% (517/517), 188.99 MiB | 21.11 MiB/s, done.
Resolving deltas: 100% (214/214), done.
Checking out files: 100% (223/223), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          RL_VPP_Thesis/
Algorithm_simulator_notebooks/    trained_models/
data/                             VPP_environment.py
EV_experiment_notebooks/          VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  wandb/
README.md


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7fcac2e1b750>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27007.69 , Grid_used_en=kWh  43158.77 , RE-to-vehicle_unused_en=kWh  16151.08 , Total_selling_cost=€  1078.01 , Grid_cost=€  1531.23 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27555.08 , Grid_used_en=kWh  43998.74 , RE-to-vehicle_unused_en=kWh  16443.66 , Total_selling_cost=€  1066.83 , Grid_cost=€  1534.54 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2159.48 , Grid_used_en=KWh  1830.08 , RE-to-vehicle_unused_en=KWh  3989.56 , Total_selling_cost=€  -47.06 , Grid_cost=€  61.15 
 EV_INFO: Av.EV_energy_leaving=kWh  64.85 , Std.EV_energy_leaving=kWh  23.63 , EV_departures =  1304 , EV_queue_left =  0
SCORE:  Cumulative_reward= 450311.79 - Step_rewars (load_t= 406628.79, EVs_energy_t= 13332.76)
 - Final_rewards (Av.EVs_energy= 19602.05, Grid_used_en= -881.38, RE-to-vehicle_unused_en= -799.13, Grid_cost= 12428.69)
Episode:1 Score:450311.78659025


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  40.230129  40.168789  72.736656  48.536137   
2022-01-01 00:15:00  40.480129  39.688843  72.256706  48.786137   
2022-01-01 00:30:00  40.730129  39.149494  71.717361  49.036137   
2022-01-01 00:45:00  40.980129  38.634487  71.202354  49.286137   
2022-01-01 01:00:00  41.230129  38.251705  70.819572  49.536137   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  78.657578  57.630402   0.000000  65.680031   
2022-06-06 05:00:00  78.407578  59.238220   0.000000  67.287849   
2022-06-06 05:15:00  78.157578  60.984695   0.000000  69.034325   
2022-06-06 05:30:00  79.204857  62.031975   0.000000  70.081604   
2022-06-06 05:45:00  80.252045  63.079166   0.000000  71.128792   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [3907, 3910, 3908, 3909]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3907, 3910, 3908, 3909]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3907, 3910, 3908, 3909]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3907, 3910, 3908, 3909]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00     [4456, 4455, 0, 4457]  [2, 1, 2, 1]   
2022-06-06 05:00:00     [4456, 4455, 0, 4457]  [2, 1, 2, 1]   
2022-06-06 05:15:00     [4456, 4455, 0, 4457]  [1, 1, 2, 1]   
2022-06-06 05:30:00     [4456, 4455, 0, 4457]  [1, 1, 2, 1]   
2022-06-06 05:45:00     [4456, 4455, 0, 4457]  [1, 1, 2, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00    [False, True, False, True]        9.210859   
2022-06-06 05:00:00    [False, True, False, True]       12.862564   
2022-06-06 05:15:00     [True, True, False, True]       13.971797   
2022-06-06 05:30:00     [True, True, False, True]       12.567360   
2022-06-06 05:45:00     [True, True, False, True]       12.566284   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  8.082625e-01         15.0   0.000000   
2022-01-01 00:15:00          -3.839584  0.000000e+00         15.0   0.000000   
2022-01-01 00:30:00          -4.314783  0.000000e+00         15.0   0.000000   
2022-01-01 00:45:00          -4.120053  4.440892e-16         15.0   0.000000   
2022-01-01 01:00:00          -3.062254  0.000000e+00         15.0 -84.303328   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000e+00         15.0   0.000000   
2022-06-06 05:00:00          -1.000000  0.000000e+00         15.0   0.000000   
2022-06-06 05:15:00          -1.000000  0.000000e+00         15.0   0.000000   
2022-06-06 05:30:00           0.000000  1.776357e-15         15.0   0.000000   
2022-06-06 05:45:00           0.000000  0.000000e+00         15.0   0.000000   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00 -69.303328  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5217, Arrival time: 2022-01-01 08:30:00, Parking_time: 24, Leaving_time: 2022-01-02 08:30:00, SOC: 0.4911805704655395, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6520, Arrival time: 2022-12-31 14:45:00, Parking_time: 24, Leaving_time: 2023-01-01 14:45:00, SOC: 0.46036058800325536, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en=kWh  2136.67 , RE-to-vehicle_unused_en=kWh  -32222.06 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17762.81 , Grid_used_en=kWh  38900.53 , RE-to-vehicle_unused_en=kWh  21137.72 , Total_selling_cost=€  832.78 , Grid_cost=€  1698.35 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18998.75 , Grid_used_en=kWh  39294.58 , RE-to-vehicle_unused_en=kWh  20295.83 , Total_selling_cost=€  897.29 , Grid_cost=€  1714.52 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4481.38 , Grid_used_en=KWh  886.49 , RE-to-vehicle_unused_en=KWh  5367.87 , Total_selling_cost=€  -156.28 , Grid_cost=€  38.89 
 EV_INFO: Av.EV_energy_leaving=kWh  69.61 , Std.EV_energy_leaving=kWh  23.72 , EV_departures =  1301 , EV_queue_left =  0
SCORE:  Cumulative_reward= 473086.0 - Step_rewars (load_t= 404785.82, EVs_energy_t= 32173.12)
 - Final_rewards (Av.EVs_energy= 21750.66, Grid_used_en= -104.49, RE-to-vehicle_unused_en= -1209.03, Grid_cost= 15689.92)
Episode:1 Score:473085.9995863403


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0    1          2          3              EVs_id  \
time                                                                      
2022-01-01 00:00:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 00:30:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 00:45:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
2022-01-01 01:00:00  0.0  0.0   0.000000   0.000000        [0, 0, 0, 0]   
...                  ...  ...        ...        ...                 ...   
2022-06-06 04:45:00  0.0  0.0  60.602219  58.823696  [0, 0, 8405, 8406]   
2022-06-06 05:00:00  0.0  0.0  62.329842  60.551319  [0, 0, 8405, 8406]   
2022-06-06 05:15:00  0.0  0.0  64.035263  62.256737  [0, 0, 8405, 8406]   
2022-06-06 05:30:00  0.0  0.0  65.928825  64.150299  [0, 0, 8405, 8406]   
2022-06-06 05:45:00  0.0  0.0  67.581367  65.802841  [0, 0, 8405, 8406]   

                          actions                   mask_truth  \
time                                                             
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 01:00:00  [2, 1, 1, 0]  [False, False, False, True]   
...                           ...                          ...   
2022-06-06 04:45:00  [0, 2, 1, 1]    [True, False, True, True]   
2022-06-06 05:00:00  [0, 2, 1, 1]    [True, False, True, True]   
2022-06-06 05:15:00  [0, 2, 1, 1]    [True, False, True, True]   
2022-06-06 05:30:00  [0, 2, 1, 1]    [True, False, True, True]   
2022-06-06 05:45:00  [0, 2, 1, 1]    [True, False, True, True]   

                     ev_charged_pwr  ev_discharged_pwr      load  load_reward  \
time                                                                            
2022-01-01 00:00:00        0.000000                0.0 -2.905362    -4.756565   
2022-01-01 00:15:00        0.000000                0.0 -3.853939    -4.913813   
2022-01-01 00:30:00        0.000000                0.0 -3.948288    -3.968978   
2022-01-01 00:45:00        0.000000                0.0 -3.381387    -3.182532   
2022-01-01 01:00:00        0.000000                0.0 -2.909519    -5.809955   
...                             ...                ...       ...          ...   
2022-06-06 04:45:00       10.977419                0.0  0.000000    15.000000   
2022-06-06 05:00:00       13.820987                0.0  0.000000    15.000000   
2022-06-06 05:15:00       13.643344                0.0  0.000000    15.000000   
2022-06-06 05:30:00       15.148509                0.0  0.000000    15.000000   
2022-06-06 05:45:00       13.220361                0.0  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.756565  
2022-01-01 00:15:00        0.0  -4.913813  
2022-01-01 00:30:00        0.0  -3.968978  
2022-01-01 00:45:00        0.0  -3.182532  
2022-01-01 01:00:00        0.0  -5.809955  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 9129, Arrival time: 2022-01-01 02:45:00, Parking_time: 23.94913134936895, Leaving_time: 2022-01-02 02:41:56.872858, SOC: 0.6237658409658192, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 10432, Arrival time: 2022-12-31 16:00:00, Parking_time: 24, Leaving_time: 2023-01-01 16:00:00, SOC: 0.4947700484368994, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en=kWh  1556.25 , RE-to-vehicle_unused_en=kWh  -35673.95 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13578.06 , Grid_used_en=kWh  36038.48 , RE-to-vehicle_unused_en=kWh  22460.42 , Total_selling_cost=€  675.61 , Grid_cost=€  1502.03 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14497.87 , Grid_used_en=kWh  36192.48 , RE-to-vehicle_unused_en=kWh  21694.61 , Total_selling_cost=€  709.33 , Grid_cost=€  1505.33 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  77.36
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6651.43 , Grid_used_en=KWh  786.16 , RE-to-vehicle_unused_en=KWh  7437.59 , Total_selling_cost=€  -234.31 , Grid_cost=€  32.46 
 EV_INFO: Av.EV_energy_leaving=kWh  71.24 , Std.EV_energy_leaving=kWh  22.96 , EV_departures =  1301 , EV_queue_left =  0
SCORE:  Cumulative_reward= 450110.2 - Step_rewars (load_t= 377541.05, EVs_energy_t= 38357.25)
 - Final_rewards (Av.EVs_energy= 21057.81, Grid_used_en= -70.27, RE-to-vehicle_unused_en= -2678.08, Grid_cost= 15902.44)
Episode:1 Score:450110.19701283844


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0    1    2          3                EVs_id  \
time                                                                        
2022-01-01 00:00:00   0.000000  0.0  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000  0.0  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000  0.0  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000  0.0  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000  0.0  0.0   0.000000          [0, 0, 0, 0]   
...                        ...  ...  ...        ...                   ...   
2022-06-06 03:30:00  74.915619  0.0  0.0  60.456821  [12281, 0, 0, 12282]   
2022-06-06 03:45:00  75.425743  0.0  0.0  60.966949  [12281, 0, 0, 12282]   
2022-06-06 04:00:00  76.215393  0.0  0.0  61.756599  [12281, 0, 0, 12282]   
2022-06-06 04:15:00  76.976791  0.0  0.0  62.517994  [12281, 0, 0, 12282]   
2022-06-06 04:30:00  77.855820  0.0  0.0  63.397018  [12281, 0, 0, 12282]   

                          actions                   mask_truth  \
time                                                             
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True]   
...                           ...                          ...   
2022-06-06 03:30:00  [1, 2, 2, 1]   [True, False, False, True]   
2022-06-06 03:45:00  [1, 2, 2, 1]   [True, False, False, True]   
2022-06-06 04:00:00  [1, 2, 2, 1]   [True, False, False, True]   
2022-06-06 04:15:00  [1, 2, 2, 1]   [True, False, False, True]   
2022-06-06 04:30:00  [1, 1, 2, 1]   [True, False, False, True]   

                     ev_charged_pwr  ev_discharged_pwr      load  load_reward  \
time                                                                            
2022-01-01 00:00:00        0.000000                0.0 -3.111307    -3.632348   
2022-01-01 00:15:00        0.000000                0.0 -3.179409    -3.489296   
2022-01-01 00:30:00        0.000000                0.0 -3.093578    -3.630143   
2022-01-01 00:45:00        0.000000                0.0 -3.178086    -6.178641   
2022-01-01 01:00:00        0.000000                0.0 -5.296505    -5.530825   
...                             ...                ...       ...          ...   
2022-06-06 03:30:00        4.212326                0.0  0.000000    15.000000   
2022-06-06 03:45:00        4.081013                0.0  0.000000    15.000000   
2022-06-06 04:00:00        6.317198                0.0  0.000000    15.000000   
2022-06-06 04:15:00        6.091167                0.0  0.000000    15.000000   
2022-06-06 04:30:00        7.032209                0.0  0.000000    -2.065270   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -3.632348  
2022-01-01 00:15:00        0.0  -3.489296  
2022-01-01 00:30:00        0.0  -3.630143  
2022-01-01 00:45:00        0.0  -6.178641  
2022-01-01 01:00:00        0.0  -5.530825  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  -2.065270  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

In [55]:
env.plot_VPP_supply_demand()

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

In [63]:
#env.close()